In [2]:
import json
with open('E:\dataset.json', 'r', encoding='utf-8') as f:
    data = json.load(f)
data

[{'sentence': '列出与药房“Pharma56”或“Pharma57”相关的所有资产',
  'annotations': [{'token': '所有(*)', 'label': 'Attribute'},
   {'token': '资产(assets)', 'label': 'Object'},
   {'token': "药房'Pharma56'(pharmacies_id = 'Pharma56')", 'label': 'Restrict'},
   {'token': "药房'Pharma57'(pharmacies_id = 'Pharma57')", 'label': 'Restrict'},
   {'golden sql': "SELECT * FROM assets WHERE pharmacies_id = 'Pharma56' OR pharmacies_id = 'Pharma57'"}]},
 {'sentence': '查找在“2025-09-01”之后或“2023-12-31”之前带有 Trial_ends_at 的设施',
  'annotations': [{'token': '*', 'label': 'Attribute'},
   {'token': '设施(facilities)', 'label': 'Object'},
   {'token': 'Trial_ends_at(trial_ends_at)', 'label': 'Restrict'},
   {'token': "'2025-09-01'", 'label': 'Restrict'},
   {'token': "'2023-12-31'", 'label': 'Restrict'},
   {'golden sql': "SELECT * FROM facilities WHERE trial_ends_at > '2025-09-01' OR trial_ends_at < '2023-12-31'"}]},
 {'sentence': '获取“2023-01-01”之后的created_at和“2023-12-21”之前的activate_at的药房',
  'annotations': [{'token': '*', 'label

In [ ]:
tokenizer=custom_tokenizer, lowercase=False, stop_words=stop_words, token_pattern=None

In [1]:
from sklearn.feature_extraction.text import TfidfVectorizer

# 定义停用词
stop_words = ['“', '”', ',', '、', "'", '/', '在', '的', '分', 'km/h', '元', '是', '有', '与', '个', '次', '万', '米', '克', '平方米', '英寸', '年', '件', '吨', '小时', '美金', '公里', '立方米', '千克', 'mAh', '度', '公顷', '星', '人', '公里', '单位', '显示', '获取', '列出', '检索', '找出', '获取', '统计', '检索', '在', '从', '列出 ', '计算', '搜索', '按', '查找', '提供 ', '提供', '找到', '选择', '查询', '为', '显示', '列举', '检索 ', '从 ', '给', '确定', '找', '获取 ', '展示', '列出']
# 原始分词结果
tokens = [['显示', '所有', '价格', '超过', '100', '元', '的', '书籍', '名称']]

# 预处理分词结果，移除停用词和标点
preprocessed_tokens = [[word for word in sentence if word not in stop_words] for sentence in tokens]

# 使用自定义的分词函数（这里即是直接使用预处理后的分词结果）
def custom_tokenizer(doc):
    return doc

# 创建TF-IDF向量生成器，注意这里tokenizer=lambda x: x表示输入已经是预处理后的分词列表
vectorizer = TfidfVectorizer(tokenizer=custom_tokenizer, lowercase=False, preprocessor=lambda x: x)

# 应用TF-IDF算法（由于输入已经预处理并分词，这里的数据flat_tokens不再是单个字符串，而是预处理后的分词列表）
flat_tokens = [t for sub_list in preprocessed_tokens for t in sub_list]  # 将嵌套列表转换为平面列表
tfidf_matrix = vectorizer.fit_transform([flat_tokens])
feature_names = vectorizer.get_feature_names_out()

# 将TF-IDF矩阵和特征名结合，打印结果
for idx, feature in enumerate(feature_names):
    print(feature, tfidf_matrix[0, idx])

100 0.4082482904638631
书籍 0.4082482904638631
价格 0.4082482904638631
名称 0.4082482904638631
所有 0.4082482904638631
超过 0.4082482904638631


C:\Users\Marshall\anaconda3\envs\new\lib\site-packages\sklearn\feature_extraction\text.py:525: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


In [4]:
from sklearn.feature_extraction.text import TfidfVectorizer
import torch
from ltp import LTP
import json

def segment_sentence(sentence):
    words = ltp.pipeline([sentence], tasks=["cws"], return_dict=False)
    return words

def custom_tokenizer(word):
    return word

ltp = LTP("E:\\papercode\\model\\base2")

if torch.cuda.is_available():
    # ltp.cuda()
    ltp.to("cuda")

# 加载数据
with open('E:\dataset.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

# #加载停用词数据
# with open('E:\papercode\stopwords\stop_word.txt', 'r', encoding='utf-8') as file:
#     stop_words = [line.strip() for line in file.readlines()]

# stop_words = stop_words.append("' ")
stop_words = ['“', '”', ',', '、', "'", '/', "' ", '。', '在', '的', '分', 'km/h', '元', '是', '有', '与', '个', '次', '万', '米', '克', '平方米', '英寸', '年', '件', '吨', '小时', '美金', '公里', '立方米', '千克', 'mAh', '度', '公顷', '星', '人', '公里', '单位', '显示', '获取', '列出', '检索', '找出', '获取', '统计', '检索', '在', '从', '列出 ', '计算', '搜索', '按', '查找', '提供 ', '提供', '找到', '选择', '查询', '为', '显示', '列举', '检索 ', '从 ', '给', '确定', '找', '获取 ', '展示', '列出', '由']

keyword_extraction_results = []

vectorizer = TfidfVectorizer(tokenizer=custom_tokenizer, lowercase=False, preprocessor=lambda x: x, token_pattern=None)

for item in data:
    sentence = item['sentence']
    sentence_segment = segment_sentence(sentence)
    preprocessed_sentence = [[word for word in piece if word not in stop_words] for piece in sentence_segment[0]]
    flat_tokens = [t for sub_list in preprocessed_sentence for t in sub_list]
    tfidf_matrix = vectorizer.fit_transform([flat_tokens])
    feature_names = vectorizer.get_feature_names_out().tolist()  # 转换为Python list

    keyword_extraction_results.append({
        'sentence': sentence,
        'keyword_result': feature_names
    })
#     print(keyword_extraction_results)

with open('keyword_extraction_results.json', 'w', encoding='utf-8') as f:
    json.dump(keyword_extraction_results, f)

Loading weights from local directory


In [5]:
with open('E:\papercode\keyword_extraction_results.json', 'r', encoding='utf-8') as f:
    data = json.load(f)
data

[{'sentence': '列出与药房“Pharma56”或“Pharma57”相关的所有资产',
  'keyword_result': ['Pharma56', 'Pharma57', '或', '所有', '相关', '药房', '资产']},
 {'sentence': '查找在“2025-09-01”之后或“2023-12-31”之前带有 Trial_ends_at 的设施',
  'keyword_result': ['2023-12-31',
   '2025-09-01',
   'Trial_ends_at ',
   '之前',
   '之后',
   '带有 ',
   '或',
   '设施']},
 {'sentence': '获取“2023-01-01”之后的created_at和“2023-12-21”之前的activate_at的药房',
  'keyword_result': ['2023-01-01',
   '2023-12-21',
   'activate_at',
   'created_at',
   '之前',
   '之后',
   '和',
   '药房']},
 {'sentence': "检索 asset_type_id 'AT089' 或 asset_type_id 'AT090' 的所有资产",
  'keyword_result': ['AT089', 'AT090', 'asset_type_id ', '或 ', '所有', '资产']},
 {'sentence': "列出 Roles_id 'Role890' 和official_user_id 'OU029' 的所有用户",
  'keyword_result': ['OU029',
   'Role890',
   'Roles_id ',
   'official_user_id ',
   '和',
   '所有',
   '用户']},
 {'sentence': "检索所有official_user_id 'OU030' 或employee_id 'E3456' 的员工",
  'keyword_result': ['E3456',
   'OU030',
   'employee_id ',
   'official_user_id

In [1]:
import torch
from ltp import LTP


ltp = LTP("E:\\papercode\\model\\base2")

if torch.cuda.is_available():
    # ltp.cuda()
    ltp.to("cuda")
result = ltp.pipeline(["显示所有评分高于4的餐厅和它们的地址"], tasks=["cws", "sdp"])
word_list = result.cws[0]
head_list = result.sdp[0]['head']
label_list = result.sdp[0]['label']
print(word_list)
print(result.sdp)
print(head_list)
print(label_list)

Loading weights from local directory
['显示', '所有', '评分', '高于', '4', '的', '餐厅', '和', '它们', '的', '地址']
[{'head': [0, 7, 4, 7, 4, 4, 1, 11, 11, 9, 7], 'label': ['Root', 'SCO', 'EXP', 'dFEAT', 'MEAS', 'mDEPD', 'CONT', 'mRELA', 'FEAT', 'mDEPD', 'eCOO']}]
[0, 7, 4, 7, 4, 4, 1, 11, 11, 9, 7]
['Root', 'SCO', 'EXP', 'dFEAT', 'MEAS', 'mDEPD', 'CONT', 'mRELA', 'FEAT', 'mDEPD', 'eCOO']


In [3]:
import json
import torch
from ltp import LTP

# 加载LTP模型
ltp = LTP("E:\\papercode\\model\\base2")
# 如果可以，转移到CUDA
if torch.cuda.is_available():
    ltp.to("cuda")

def process_sentence(sentence):
    result = ltp.pipeline([sentence], tasks=["cws", "sdp"])
    word_list = result.cws[0]
    head_list = result.sdp[0]['head']
    label_list = result.sdp[0]['label']
    triples = []
    for i in range(1, len(head_list)):
        if label_list[i] != 'mPUNC':
            head_index = head_list[i]
            head_word = word_list[head_index-1] if head_index > 0 else "ROOT"
            dependent_word = word_list[i]
            relation_label = label_list[i]
            triples.append((head_word, dependent_word, relation_label))
    return triples

test = process_sentence("显示所有评分高于4的餐厅和它们的地址")
print(test)

# # 读取输入的JSON文件
# input_filename = "E:\\papercode\\test_data.json"
# with open(input_filename, 'r', encoding='utf-8') as file:
#     data = json.load(file)

# semantic_dependency_analysis_results = []

# # 对每个句子进行处理
# for item in data:
#     sentence = item["sentence"]
#     sentence_triples = process_sentence(sentence)
#     semantic_dependency_analysis_results.append({
#         "sentence": sentence,
#         "triples": sentence_triples
#     })

# # 保存结果到JSON文件
# output_filename = "semantic_dependency_analysis_results_test.json"
# with open(output_filename, 'w', encoding='utf-8') as outfile:
#     json.dump(semantic_dependency_analysis_results, outfile, ensure_ascii=False)

Loading weights from local directory
[('餐厅', '所有', 'SCO'), ('高于', '评分', 'EXP'), ('餐厅', '高于', 'dFEAT'), ('高于', '4', 'MEAS'), ('高于', '的', 'mDEPD'), ('显示', '餐厅', 'CONT'), ('地址', '和', 'mRELA'), ('地址', '它们', 'FEAT'), ('它们', '的', 'mDEPD'), ('餐厅', '地址', 'eCOO')]


In [1]:
with open('E:\papercode\semantic_dependency_analysis_results.json', 'r', encoding='utf-8') as f:
    data = json.load(f)
data[0]

FileNotFoundError: [Errno 2] No such file or directory: 'E:\\papercode\\semantic_dependency_analysis_results.json'

In [ ]:
import torch
from transformers import RobertaModel, RobertaTokenizer
import json
import numpy as np

# 加载 RoBERTa 模型和 tokenizer
tokenizer = RobertaTokenizer.from_pretrained('roberta-base')
model = RobertaModel.from_pretrained('roberta-base')

# 读取您的.json数据集
with open('E:\\papercode\\Train\\semantic_dependency_analysis_results_train.json', 'r') as f:
    data = json.load(f)

# 对 'triples'中的每一个部分的前两个进行处理
for item in data:
    triples = item['triples']
    for i, triple in enumerate(triples):
        # 对前两个词进行word embedding
        inputs = tokenizer(triple[0:2], return_tensors='pt', padding=True, truncation=True)
        outputs = model(**inputs)

        # 总的词向量可以通过对所有的最后一层的隐藏状态取平均得到
        embeddings = outputs.last_hidden_state.mean(dim=1)

        # 对最后一个词进行随机初始化
        random_vector = np.random.rand(1, 768)

        # 将word embedding和随机初始化的向量连接在一起
        triple_vector = torch.cat((embeddings, torch.tensor(random_vector)), dim=1)

        # 打印这一个triple的结果
        print(triple_vector)

In [2]:
import torch
from transformers import RobertaModel, RobertaTokenizer
import json
import numpy as np

# 定义一个线性层用于从768维降到300维
linear = torch.nn.Linear(768, 300)

# 加载 RoBERTa 模型和 tokenizer
tokenizer = RobertaTokenizer.from_pretrained('E:\\papercode\\model\\roberta-base', ignore_mismatched_sizes=True)
model = RobertaModel.from_pretrained('E:\\papercode\\model\\roberta-base')

# 读取您的.json数据集
with open('E:\\papercode\\Train\\semantic_dependency_analysis_results_train.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

# 对 'triples'中的每一个部分的前两个进行处理
for item in data:
    triples = item['triples']
    for triple in triples:
        # 对前两个词进行word embedding
        inputs = tokenizer(triple[0:2], return_tensors='pt', padding='max_length', max_length=512, truncation=True)
        outputs = model(**inputs)

        # 取最后一层的隐藏状态的平均值获取句子级的向量表示
        sentence_embedding_avg = outputs.last_hidden_state.mean(dim=1)

        # 使用线性层从768维降维到300维
        reduced_embedding = linear(sentence_embedding_avg)

        # 输出前两个部分的word embedding
        print("Reduced Embedding for:", triple[0:2], "\n", reduced_embedding)

        # 对最后一个词进行随机初始化的300维向量
        random_vector = torch.rand((1, 300))
        # 输出这个随机初始化的向量
        print("Random Vector for:", triple[2], "\n", random_vector)

Some weights of RobertaModel were not initialized from the model checkpoint at E:\papercode\model\roberta-base and are newly initialized: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Reduced Embedding for: ['农场', '所有'] 
 tensor([[-3.2337e-02,  8.9858e-03,  3.0497e-02, -1.8732e-01,  3.9444e-01,
          1.0010e-01,  2.5532e-01,  1.6241e-01, -7.0934e-02,  2.4619e-01,
         -2.3239e-01, -3.0237e-01, -1.6051e-01, -9.3218e-02,  1.8295e-01,
          1.9259e-01,  2.9851e-01,  3.7278e-02, -6.2842e-02,  3.0980e-01,
         -2.3361e-02, -3.7864e-01,  2.7287e-01, -1.7534e-01,  1.8959e-01,
         -3.6332e-01, -2.0973e-01,  2.2416e-01, -1.1862e-01, -2.0610e-01,
         -1.5149e-01, -2.0561e-01, -4.6573e-01,  1.3685e-01, -3.0489e-01,
         -3.0838e-01, -6.7642e-01,  3.1800e-01, -4.1434e-02, -7.5358e-02,
          8.3343e-02,  1.3140e-01,  1.0883e-01, -8.7205e-02, -5.9031e-01,
          3.9222e-01, -5.0486e-02,  3.8301e-01, -4.7887e-02,  4.1683e-01,
         -2.3661e-01, -3.5603e-01,  3.2424e-01,  3.0111e-02,  1.4757e-01,
          4.3320e-01, -3.1199e-01,  2.2436e-01,  2.7049e-01, -1.2787e-01,
         -3.2185e-01,  4.2679e-01,  2.7551e-02,  3.7222e-01, -1.4124e-01,


Reduced Embedding for: ['农场', '种植'] 
 tensor([[-3.2337e-02,  8.9858e-03,  3.0497e-02, -1.8732e-01,  3.9444e-01,
          1.0010e-01,  2.5532e-01,  1.6241e-01, -7.0934e-02,  2.4619e-01,
         -2.3239e-01, -3.0237e-01, -1.6051e-01, -9.3218e-02,  1.8295e-01,
          1.9259e-01,  2.9851e-01,  3.7278e-02, -6.2842e-02,  3.0980e-01,
         -2.3361e-02, -3.7864e-01,  2.7287e-01, -1.7534e-01,  1.8959e-01,
         -3.6332e-01, -2.0973e-01,  2.2416e-01, -1.1862e-01, -2.0610e-01,
         -1.5149e-01, -2.0561e-01, -4.6573e-01,  1.3685e-01, -3.0489e-01,
         -3.0838e-01, -6.7642e-01,  3.1800e-01, -4.1434e-02, -7.5358e-02,
          8.3343e-02,  1.3140e-01,  1.0883e-01, -8.7205e-02, -5.9031e-01,
          3.9222e-01, -5.0486e-02,  3.8301e-01, -4.7887e-02,  4.1683e-01,
         -2.3661e-01, -3.5603e-01,  3.2424e-01,  3.0111e-02,  1.4757e-01,
          4.3320e-01, -3.1199e-01,  2.2436e-01,  2.7049e-01, -1.2787e-01,
         -3.2185e-01,  4.2679e-01,  2.7551e-02,  3.7222e-01, -1.4124e-01,


Reduced Embedding for: ['作物', '转基因'] 
 tensor([[ 2.4125e-02,  2.2860e-01, -3.1187e-01, -1.4243e-01,  1.1430e-01,
          6.2536e-02,  2.3971e-01,  1.3149e-01,  5.5999e-02,  2.3021e-01,
         -1.7105e-01, -4.7913e-01, -3.9417e-01, -4.4561e-02,  2.5479e-02,
         -1.0962e-01,  5.0377e-01,  2.1955e-01, -1.2745e-01,  2.8832e-01,
         -9.2907e-02, -2.1038e-01, -2.9487e-02, -8.8088e-02, -2.6194e-02,
         -3.7893e-01, -4.0921e-01,  3.6547e-01, -6.5324e-02, -2.3367e-01,
         -8.2802e-02, -1.4386e-01, -1.8239e-01,  1.8997e-01, -2.2231e-01,
         -2.6696e-01, -4.4424e-01,  5.5319e-01, -2.6137e-01, -1.9850e-01,
         -4.1791e-02,  2.5958e-02,  1.3071e-01, -7.5394e-02, -3.9715e-01,
          2.4337e-01, -1.7746e-01,  1.1881e-01, -1.3843e-01, -3.2610e-01,
         -3.6013e-01, -3.0202e-01,  3.2020e-01, -9.2204e-02, -2.8282e-01,
          1.9302e-01, -1.7923e-01, -1.3605e-02,  2.3485e-01, -2.7636e-01,
         -1.5840e-02,  6.0120e-02,  2.6808e-01,  1.5665e-01, -2.0336e-01,

Reduced Embedding for: ['种植', '作物'] 
 tensor([[ 9.4953e-03,  7.5673e-02, -1.6658e-01, -1.7867e-01,  2.6423e-01,
          9.1626e-02,  2.0001e-01,  1.5457e-01,  1.1037e-01,  2.0236e-01,
         -3.1858e-01, -4.8096e-01, -2.3171e-01, -1.7148e-01,  5.6880e-02,
          1.9358e-01,  2.9621e-01,  1.4648e-01, -1.6314e-01,  3.0293e-01,
         -9.0132e-02, -4.3525e-01,  6.6317e-02, -1.8597e-01,  1.4425e-01,
         -3.2479e-01, -2.9277e-01,  3.0374e-01,  4.9955e-02, -1.0223e-01,
         -4.3458e-02, -2.9550e-01, -3.1584e-01,  1.9750e-01, -1.4082e-01,
         -4.2175e-01, -5.5147e-01,  4.8436e-01, -2.1068e-01, -1.8859e-01,
         -7.6137e-02,  9.8361e-02,  1.5238e-01, -1.8817e-01, -5.0312e-01,
          3.0357e-01, -1.6076e-01,  3.5861e-01, -2.0963e-01,  8.8170e-02,
         -2.8819e-01, -2.3048e-01,  3.5023e-01,  8.3856e-02, -8.2431e-02,
          3.1477e-01, -2.1840e-01,  5.1574e-02,  1.4819e-01, -2.9534e-01,
         -1.3699e-01,  3.7087e-01,  7.5133e-02,  2.9358e-01, -1.1407e-01,


...

Reduced Embedding for: ['多样性', '植物'] 
 tensor([[ 6.6572e-02, -3.9536e-02, -1.2024e-01, -8.8214e-02,  2.1045e-01,
          7.9824e-02,  1.4322e-01,  2.9084e-01,  2.2061e-02,  1.4709e-01,
         -2.0878e-01, -4.1890e-01, -2.7840e-01, -1.6524e-01,  1.5290e-01,
          2.5901e-01,  2.3618e-01,  1.4857e-01, -1.1430e-01,  3.2055e-01,
          1.4752e-01, -3.5561e-01,  8.5900e-02, -2.3654e-01,  3.3811e-01,
         -3.4915e-01, -2.3501e-01,  2.9990e-01, -4.5692e-02, -4.5529e-02,
         -6.8132e-02, -1.0530e-02, -4.0305e-01,  1.5002e-01, -6.9832e-02,
         -3.5408e-01, -4.4597e-01,  2.8648e-01, -7.4103e-02, -1.8687e-01,
          7.5062e-03,  2.1766e-01,  1.5815e-01, -6.2712e-02, -5.8001e-01,
          3.4058e-01, -2.0397e-01,  3.4786e-01, -1.8206e-02,  1.2722e-01,
         -3.4811e-01, -3.6970e-01,  1.8215e-01, -3.3719e-02, -3.1255e-03,
          2.5529e-01, -2.1304e-01,  5.7114e-02,  1.2302e-01, -2.4853e-01,
         -2.3555e-01,  2.5670e-01,  1.7709e-01,  2.8222e-01,  1.7539e-03,

Reduced Embedding for: ['名称', '多样性'] 
 tensor([[-1.4254e-02,  1.3229e-01, -2.4142e-01, -9.2148e-02,  1.3528e-01,
          7.3227e-02,  2.3237e-01,  1.2729e-01,  8.6365e-02,  1.7382e-01,
         -2.5994e-01, -4.7843e-01, -3.2920e-01, -3.6158e-02,  7.3127e-02,
          2.1619e-02,  3.1328e-01,  2.0728e-01, -1.7154e-01,  2.5161e-01,
         -6.4114e-02, -3.6255e-01,  2.1697e-02, -1.1544e-01,  4.1563e-02,
         -3.9539e-01, -4.0058e-01,  4.2171e-01,  1.0693e-01, -1.7450e-01,
         -1.2353e-01, -1.2967e-01, -2.9978e-01,  1.3659e-01, -1.2387e-01,
         -3.7134e-01, -4.7662e-01,  5.2378e-01, -1.8069e-01, -2.3317e-01,
         -3.6171e-02,  6.0276e-02,  5.5367e-02, -1.0869e-01, -4.5049e-01,
          3.0400e-01, -1.7185e-01,  3.2574e-01, -1.0478e-01, -5.1272e-02,
         -3.2004e-01, -2.7003e-01,  3.1128e-01, -1.1577e-03, -1.3466e-01,
          3.2068e-01, -2.1506e-01, -1.5491e-02,  2.3134e-01, -2.6377e-01,
         -6.9336e-02,  1.9534e-01,  1.7147e-01,  2.2063e-01, -9.4874e-02,

Reduced Embedding for: ['找', '出'] 
 tensor([[ 5.9463e-03, -1.2374e-02, -2.1315e-02, -2.1679e-01,  4.7295e-01,
          2.7422e-01,  4.5961e-01,  3.9092e-01, -4.5951e-02,  3.2378e-01,
         -3.0231e-01, -5.1960e-01, -4.5961e-01, -6.8436e-02,  1.8694e-01,
         -3.7953e-02,  5.6278e-01,  1.6314e-01, -1.6302e-01,  4.3100e-01,
         -1.6546e-01, -4.4095e-01,  2.3437e-01,  7.2734e-02,  8.5944e-02,
         -2.0609e-01, -2.0701e-01,  5.0073e-01,  5.8922e-02, -2.0458e-01,
         -4.0050e-02, -9.9880e-03, -5.4789e-02, -1.0940e-02, -3.4052e-01,
         -3.2662e-01, -5.6057e-01,  5.5502e-01, -6.1699e-02, -2.9540e-01,
          3.7784e-02,  1.4297e-01,  3.3645e-02,  1.1516e-02, -5.9182e-01,
          2.6366e-01, -4.1123e-02,  2.6412e-01, -3.6012e-01,  2.8892e-02,
         -1.7303e-01, -1.5735e-01,  2.9637e-01, -1.6921e-01, -1.5093e-01,
          3.6308e-01, -1.8223e-01,  2.8805e-01,  2.0963e-01, -2.1176e-01,
         -3.0412e-01,  5.6872e-01,  1.6847e-01,  7.0606e-02, -3.2266e-01,
  

Reduced Embedding for: ['工厂', '所有'] 
 tensor([[-1.7785e-02,  1.8892e-01, -2.2454e-01, -8.9174e-02,  9.0113e-02,
          4.4338e-02,  2.2612e-01,  1.3202e-01,  1.0534e-01,  3.0226e-01,
         -2.0690e-01, -4.8778e-01, -3.7544e-01, -1.5408e-01,  7.3784e-02,
          2.0671e-02,  4.5175e-01,  1.9704e-01, -1.1138e-01,  2.7973e-01,
         -1.1811e-03, -3.0760e-01,  2.2337e-02, -2.4563e-01,  2.0617e-02,
         -3.8545e-01, -3.9152e-01,  3.9122e-01, -9.8803e-02, -1.5683e-01,
         -7.9381e-02, -1.0648e-01, -2.9615e-01,  1.6277e-01, -1.0250e-01,
         -2.6490e-01, -4.2849e-01,  4.6365e-01, -2.0177e-01, -2.7159e-01,
         -2.2386e-03,  2.4253e-02,  1.6608e-01, -4.8094e-02, -4.7078e-01,
          2.8634e-01, -1.7699e-01,  2.2614e-01, -6.4587e-02, -8.0400e-02,
         -3.2755e-01, -3.6945e-01,  3.6497e-01, -7.9803e-02, -2.0928e-01,
          2.5207e-01, -1.3828e-01, -4.8757e-02,  2.0032e-01, -2.8223e-01,
         -7.2517e-02,  1.8231e-01,  2.1814e-01,  2.6322e-01, -3.6727e-02,


KeyboardInterrupt: 

In [2]:
import json

with open('E:\\papercode\\Train\\train_data.json', 'r', encoding='utf-8') as f:
    data = json.load(f)
data

[{'sentence': '查询所有种植转基因作物的农场及其平均每亩产量',
  'keyword_result': ['产量', '作物', '农场', '及其', '平均', '所有', '每亩', '种植', '转基因']},
 {'sentence': '检索姓名以“A”结尾的活动人员角色',
  'keyword_result': ['A', '人员', '以', '姓名', '活动', '结尾', '角色']},
 {'sentence': '找出所有电影票价低于50元的电影名称和票价',
  'keyword_result': ['50', '低于', '出', '名称', '和', '所有', '电影', '票价']},
 {'sentence': '从员工表中检索员工的平均年龄',
  'keyword_result': ['中', '员工', '平均', '年龄', '表']},
 {'sentence': "检索所有official_user_id 'OU003' 或employee_id 'E4567' 的员工",
  'keyword_result': ['E4567',
   'OU003',
   'employee_id ',
   'official_user_id ',
   '员工',
   '或',
   '所有']},
 {'sentence': '显示所有安装智能视频监控系统的便利店名称和减少的盗窃案件数',
  'keyword_result': ['便利店',
   '减少',
   '名称',
   '和',
   '安装',
   '所有',
   '数',
   '智能',
   '案件',
   '监控',
   '盗窃',
   '系统',
   '视频']},
 {'sentence': '显示所有外语类课程的课程名称和授课教师',
  'keyword_result': ['名称', '和', '外语类', '所有', '授课', '教师', '课程']},
 {'sentence': '列举所有计算机的品牌和性能',
  'keyword_result': ['和', '品牌', '性能', '所有', '计算机']},
 {'sentence': '查询所有生产有机肥料的公司及其肥料的平均氮含量',

In [3]:
import json

with open('E:\\papercode\\Train\\semantic_dependency_analysis_results_train.json', 'r', encoding='utf-8') as f:
    data = json.load(f)
data

[{'sentence': '查询所有种植转基因作物的农场及其平均每亩产量',
  'triples': [['农场', '所有', 'SCO'],
   ['农场', '种植', 'rAGT'],
   ['作物', '转基因', 'FEAT'],
   ['种植', '作物', 'CONT'],
   ['种植', '的', 'mDEPD'],
   ['查询', '农场', 'CONT'],
   ['产量', '及其', 'mRELA'],
   ['产量', '平均', 'FEAT'],
   ['产量', '每亩', 'SCO'],
   ['农场', '产量', 'eCOO']]},
 {'sentence': '检索姓名以“A”结尾的活动人员角色',
  'triples': [['检索', '姓名', 'CONT'],
   ['A', '以', 'mRELA'],
   ['结尾', 'A', 'EXP'],
   ['人员', '结尾', 'rEXP'],
   ['结尾', '的', 'mDEPD'],
   ['人员', '活动', 'FEAT'],
   ['角色', '人员', 'FEAT'],
   ['姓名', '角色', 'eCOO']]},
 {'sentence': '找出所有电影票价低于50元的电影名称和票价',
  'triples': [['找', '出', 'mDEPD'],
   ['票价', '所有', 'SCO'],
   ['票价', '电影', 'FEAT'],
   ['低于', '票价', 'EXP'],
   ['名称', '低于', 'dFEAT'],
   ['元', '50', 'MEAS'],
   ['低于', '元', 'MEAS'],
   ['低于', '的', 'mDEPD'],
   ['名称', '电影', 'FEAT'],
   ['找', '名称', 'CONT'],
   ['票价', '和', 'mRELA'],
   ['名称', '票价', 'eCOO']]},
 {'sentence': '从员工表中检索员工的平均年龄',
  'triples': [['表', '员工', 'FEAT'],
   ['检索', '表', 'LOC'],
   ['表', '中', '

In [5]:
import torch
import json

# 读取JSON文件
def load_data_from_json(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        data = json.load(file)
    return data

# 文件路径
file_path = "semantic_dependency_analysis_results_train.json"

# 加载数据
data = load_data_from_json(file_path)

# 初始化一个字典来存储每个独特的最后一项及其对应的随机向量
unique_last_item_vectors = {}

# 处理每个三元组
for item in data:
    triples = item['triples']
    for triple in triples:
        # 检查字典中是否已经有了当前最后一项的随机向量
        if triple[2] not in unique_last_item_vectors:
            # 如果没有，则为其创建一个新的随机向量
            unique_last_item_vectors[triple[2]] = torch.rand((1, 300))

# 这时 unique_last_item_vectors 字典包含了每个独特的最后一项及其对应的随机向量
# print("Unique Last Item Vectors:", unique_last_item_vectors)
for key, values in unique_last_item_vectors.items():
    print(values)

tensor([[0.1681, 0.3017, 0.2183, 0.4455, 0.3807, 0.5114, 0.9538, 0.1697, 0.3414,
         0.7620, 0.2903, 0.0775, 0.0358, 0.0549, 0.6260, 0.0517, 0.3483, 0.2911,
         0.8890, 0.7366, 0.5229, 0.2157, 0.5906, 0.1300, 0.4655, 0.4371, 0.1900,
         0.5919, 0.9362, 0.5437, 0.4083, 0.3078, 0.0606, 0.8871, 0.7479, 0.5573,
         0.9422, 0.4491, 0.5709, 0.8336, 0.0786, 0.3698, 0.7877, 0.4038, 0.1389,
         0.4020, 0.2994, 0.2116, 0.6810, 0.2442, 0.0659, 0.8254, 0.7338, 0.3610,
         0.8719, 0.3306, 0.0606, 0.7356, 0.0036, 0.6019, 0.8115, 0.6788, 0.5731,
         0.8345, 0.2413, 0.4485, 0.5457, 0.1498, 0.8969, 0.0397, 0.2161, 0.8721,
         0.2080, 0.6071, 0.1715, 0.3822, 0.1950, 0.4206, 0.6453, 0.0696, 0.7416,
         0.4615, 0.4096, 0.5033, 0.5766, 0.8683, 0.7748, 0.3750, 0.4318, 0.1164,
         0.8472, 0.5833, 0.5372, 0.0162, 0.7663, 0.6124, 0.3042, 0.8326, 0.5729,
         0.2616, 0.7293, 0.9475, 0.9658, 0.1646, 0.1199, 0.0069, 0.6906, 0.4995,
         0.7357, 0.3129, 0.9

In [4]:
import json

with open('E:\\papercode\\Train\\train_data.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

data
# 提取关键词结果
# keyword_result = data[0]['keyword_result']
# keyword_result

[{'sentence': '查询所有种植转基因作物的农场及其平均每亩产量',
  'keyword_result': ['产量', '作物', '农场', '及其', '平均', '所有', '每亩', '种植', '转基因']},
 {'sentence': '检索姓名以“A”结尾的活动人员角色',
  'keyword_result': ['A', '人员', '以', '姓名', '活动', '结尾', '角色']},
 {'sentence': '找出所有电影票价低于50元的电影名称和票价',
  'keyword_result': ['50', '低于', '出', '名称', '和', '所有', '电影', '票价']},
 {'sentence': '从员工表中检索员工的平均年龄',
  'keyword_result': ['中', '员工', '平均', '年龄', '表']},
 {'sentence': "检索所有official_user_id 'OU003' 或employee_id 'E4567' 的员工",
  'keyword_result': ['E4567',
   'OU003',
   'employee_id ',
   'official_user_id ',
   '员工',
   '或',
   '所有']},
 {'sentence': '显示所有安装智能视频监控系统的便利店名称和减少的盗窃案件数',
  'keyword_result': ['便利店',
   '减少',
   '名称',
   '和',
   '安装',
   '所有',
   '数',
   '智能',
   '案件',
   '监控',
   '盗窃',
   '系统',
   '视频']},
 {'sentence': '显示所有外语类课程的课程名称和授课教师',
  'keyword_result': ['名称', '和', '外语类', '所有', '授课', '教师', '课程']},
 {'sentence': '列举所有计算机的品牌和性能',
  'keyword_result': ['和', '品牌', '性能', '所有', '计算机']},
 {'sentence': '查询所有生产有机肥料的公司及其肥料的平均氮含量',

In [9]:
import torch
from transformers import RobertaModel, RobertaTokenizer
import json
import numpy as np

# 定义一个线性层用于从768维降到300维
linear = torch.nn.Linear(768, 300)

# 加载 RoBERTa 模型和 tokenizer
tokenizer = RobertaTokenizer.from_pretrained('E:\\papercode\\model\\roberta-base', ignore_mismatched_sizes=True)
model = RobertaModel.from_pretrained('E:\\papercode\\model\\roberta-base')

# 读取.json数据集
with open('E:\\papercode\\Train\\train_data.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

# 对 'keyword_result' 中的每一个词进行处理
for item in data:
    keywords = item['keyword_result']
    for keyword in keywords:
        # 对每个词进行word embedding
        inputs = tokenizer(keyword, return_tensors='pt', padding='max_length', max_length=512, truncation=True)
        outputs = model(**inputs)

        # 取最后一层的隐藏状态的平均值获取词级的向量表示
        word_embedding_avg = outputs.last_hidden_state.mean(dim=1)

        # 使用线性层从768维降维到300维
        reduced_embedding = linear(word_embedding_avg)

        # 输出每个词的word embedding
        print("Reduced Embedding for:", keyword, "\n", reduced_embedding)

Some weights of RobertaModel were not initialized from the model checkpoint at E:\papercode\model\roberta-base and are newly initialized: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Reduced Embedding for: 产量 
 tensor([[-2.3980e-01,  9.8725e-02, -2.1348e-01,  1.8829e-01, -3.1089e-01,
          4.6135e-02,  1.4829e-01, -2.9339e-02,  2.3585e-01, -5.3191e-02,
          1.8452e-02, -3.9103e-02,  2.3006e-01,  1.6908e-01, -3.7045e-01,
         -1.0552e-01,  1.2676e-01, -2.4574e-01, -9.4287e-02,  1.6947e-01,
         -2.4516e-01,  3.6265e-01, -1.0795e-01, -1.9565e-03,  1.0083e-01,
          1.7185e-01, -8.8963e-02,  1.4169e-01, -2.1090e-01, -4.9648e-02,
          1.5896e-01, -2.6457e-01,  9.8639e-02,  1.1418e-01,  2.3910e-01,
          5.9847e-03, -8.7711e-02,  4.9570e-01,  2.7339e-01,  2.5011e-01,
          2.2449e-01,  1.8375e-01, -1.2415e-01,  1.5425e-01,  1.5909e-01,
          1.9011e-01, -8.6663e-02,  1.9472e-01, -3.8974e-01, -4.1635e-01,
         -1.3167e-01, -2.4556e-01,  1.1672e-01, -5.2571e-01, -3.8499e-01,
         -1.8673e-01,  2.9215e-01, -5.8836e-02,  6.9188e-02, -1.7199e-01,
         -1.5692e-01, -2.6815e-01, -6.7475e-02,  1.9331e-01,  7.2609e-02,
         -

Reduced Embedding for: 及其 
 tensor([[-0.2203,  0.0385, -0.2065,  0.2047, -0.1975, -0.0481,  0.1190,  0.0936,
          0.1388, -0.3452,  0.0923,  0.0642,  0.1911,  0.2082, -0.4423, -0.0694,
          0.2179, -0.2218, -0.3574, -0.0022, -0.2203,  0.4004, -0.0456, -0.0047,
          0.2065,  0.1139, -0.1830,  0.0436,  0.0221, -0.0446,  0.2066, -0.3581,
         -0.1062,  0.1406,  0.1033, -0.2094, -0.0473,  0.4885,  0.2428,  0.2891,
          0.3003,  0.2963, -0.2128,  0.1523,  0.1130,  0.1559, -0.2585,  0.3954,
         -0.3931, -0.2586, -0.2553, -0.2299,  0.2498, -0.5958, -0.4049, -0.0811,
          0.4746, -0.0329,  0.0717, -0.0853, -0.1562, -0.2641,  0.0175,  0.2551,
          0.0568, -0.3925, -0.7228, -0.2152, -0.3554,  0.0340, -0.1780, -0.3135,
          0.0497,  0.4330,  0.2202, -0.3594,  0.0636, -0.2167,  0.0890,  0.3077,
          0.2127, -0.2861, -0.3249,  0.2115,  0.1422,  0.5693,  0.0201,  0.5129,
         -0.1991, -0.0913, -0.3258, -0.0126, -0.3460, -0.1537,  0.7143, -0.4495,


Reduced Embedding for: 每亩 
 tensor([[-0.1963,  0.2330, -0.2489,  0.0175, -0.1464,  0.1467,  0.1402, -0.3071,
          0.0939,  0.1609,  0.0607,  0.1018,  0.3022,  0.1231, -0.2615, -0.1066,
          0.1352, -0.1952, -0.1245,  0.1790, -0.3640,  0.3265, -0.1550, -0.0695,
          0.2070,  0.0374, -0.1184,  0.0901, -0.0195, -0.0522,  0.2280, -0.0951,
          0.0782,  0.1319,  0.2567,  0.0978, -0.1331,  0.3876,  0.2490,  0.2139,
          0.0811,  0.2768, -0.1481,  0.1334,  0.0773,  0.2803, -0.2248, -0.0628,
         -0.4719, -0.2205, -0.1404, -0.4925,  0.1163, -0.4423, -0.3965, -0.2498,
          0.3012,  0.0495,  0.2021, -0.0085, -0.2479, -0.2175, -0.2480,  0.2840,
          0.1469, -0.3462, -0.4916, -0.3495, -0.2212, -0.0147, -0.3221, -0.2963,
         -0.0943,  0.3520, -0.0288, -0.2150,  0.1954, -0.0361,  0.1347,  0.1661,
         -0.0090, -0.3473, -0.3798,  0.0759,  0.2757,  0.4849, -0.1282,  0.3930,
         -0.0453, -0.1246, -0.1914,  0.1091, -0.0345, -0.2946,  0.5265, -0.0738,


Reduced Embedding for: A 
 tensor([[-2.4611e-01,  2.5651e-01, -2.9186e-01,  3.2681e-01, -3.0963e-01,
         -1.5758e-01,  2.7283e-01, -3.6497e-01,  1.8856e-01, -9.7988e-04,
          1.4055e-02,  2.2448e-01,  1.8031e-01,  4.2308e-02, -2.7355e-02,
         -3.2158e-01,  1.1402e-01, -2.0855e-01, -1.9580e-01,  1.3229e-01,
         -1.9405e-01,  2.4353e-01, -1.1291e-01,  1.4207e-01,  3.9647e-02,
          1.8741e-01, -1.4490e-01,  1.3191e-01, -6.4652e-02,  9.3254e-02,
          1.4592e-01, -1.7833e-01, -1.9290e-01,  7.6817e-02,  2.5663e-03,
         -1.4543e-02, -2.0658e-01,  3.4736e-01,  2.7990e-01,  2.6930e-01,
          3.7666e-01, -3.5066e-02, -1.4357e-01,  1.3856e-01,  1.2465e-01,
          1.4608e-01, -1.5431e-01, -5.9018e-02, -2.1134e-01, -2.2350e-01,
         -6.7329e-03, -3.5009e-01,  1.6569e-01, -4.9745e-01, -4.2820e-01,
         -2.0061e-01,  1.5359e-01,  6.6556e-02,  8.4231e-02, -1.7788e-01,
         -1.7202e-02, -5.4416e-01, -2.6551e-01,  1.7754e-01,  1.6418e-03,
         -2

...

Reduced Embedding for: 结尾 
 tensor([[-0.1647,  0.1412, -0.2281,  0.1432, -0.3428, -0.0013,  0.2235, -0.1322,
          0.1663,  0.0254,  0.0389,  0.0234,  0.2070,  0.2190, -0.3054, -0.1368,
          0.0160, -0.2926, -0.1724,  0.1405, -0.3903,  0.3794, -0.1218, -0.1228,
          0.1571,  0.2877, -0.1557,  0.1554, -0.1007, -0.0035,  0.2727, -0.2195,
          0.0420,  0.1230,  0.1629,  0.0178, -0.0636,  0.4360,  0.3356,  0.1600,
          0.2425,  0.2044, -0.1345,  0.1432,  0.1100,  0.2115, -0.1229,  0.0738,
         -0.4359, -0.3266, -0.1767, -0.2805,  0.0870, -0.5507, -0.3991, -0.2000,
          0.3018, -0.0308,  0.1601, -0.0215, -0.1705, -0.3870, -0.0323,  0.2050,
          0.0934, -0.3824, -0.5313, -0.3607, -0.2957,  0.0523, -0.3794, -0.3590,
         -0.1132,  0.2834, -0.0339, -0.0488,  0.1937, -0.0611,  0.0300,  0.2334,
          0.1787, -0.3181, -0.2942,  0.1390,  0.1166,  0.5454, -0.0255,  0.5289,
         -0.2419, -0.1856, -0.2635,  0.1868, -0.1638, -0.1804,  0.6493, -0.2134,


Reduced Embedding for: 低于 
 tensor([[-2.1720e-01,  2.1537e-01, -2.3534e-01,  5.6267e-02, -1.4219e-01,
          1.1538e-01,  1.3658e-01, -3.0936e-01,  1.3393e-01,  1.1475e-01,
          7.7346e-02,  7.9495e-02,  2.5107e-01,  9.2210e-02, -2.6259e-01,
         -1.2308e-01,  1.0934e-01, -1.4730e-01, -1.0673e-01,  1.7688e-01,
         -3.6895e-01,  3.7608e-01, -1.1668e-01, -5.5937e-02,  1.6792e-01,
          4.8868e-02, -1.2302e-01,  1.2478e-01, -1.4303e-02, -3.9052e-02,
          2.2050e-01, -1.0217e-01,  9.3092e-02,  1.6775e-01,  2.6825e-01,
          5.7942e-02, -1.3605e-01,  4.1715e-01,  2.4811e-01,  1.9643e-01,
          8.8706e-02,  2.1739e-01, -1.3420e-01,  1.5079e-01,  5.0888e-02,
          2.4027e-01, -2.4376e-01, -1.8323e-02, -4.6088e-01, -2.2411e-01,
         -1.4795e-01, -4.7359e-01,  7.2206e-02, -4.5980e-01, -3.9423e-01,
         -2.1246e-01,  3.3144e-01,  4.8619e-03,  1.7166e-01, -3.4736e-02,
         -2.5385e-01, -1.8488e-01, -2.2983e-01,  3.1644e-01,  1.4792e-01,
         -

Reduced Embedding for: 和 
 tensor([[-0.2833,  0.2702, -0.2075,  0.1825, -0.3063, -0.0519,  0.2077, -0.2682,
          0.2741, -0.0218,  0.0410, -0.0441,  0.2530,  0.1937, -0.3246, -0.1409,
          0.0881, -0.2753, -0.1892,  0.0253, -0.2742,  0.4035, -0.1172, -0.0733,
          0.1186,  0.1255, -0.1859,  0.0747, -0.0822,  0.0161,  0.1508, -0.1802,
         -0.0620,  0.1216,  0.1675, -0.0569,  0.0834,  0.5134,  0.2939,  0.2371,
          0.2426,  0.1493, -0.1298,  0.1845,  0.0962,  0.2037, -0.2183,  0.0957,
         -0.3513, -0.2286, -0.1854, -0.3996,  0.0871, -0.6859, -0.4085, -0.1727,
          0.3399, -0.0793,  0.0828, -0.2071, -0.1645, -0.3223, -0.2338,  0.3203,
          0.0403, -0.3231, -0.5093, -0.3277, -0.3097,  0.0720, -0.2882, -0.4866,
          0.0087,  0.2950,  0.1941, -0.1674,  0.1480, -0.2165,  0.1009,  0.2657,
          0.1989, -0.4284, -0.3342,  0.1751,  0.1621,  0.5441, -0.0142,  0.5265,
         -0.1397, -0.2091, -0.3485,  0.0900, -0.0450, -0.3020,  0.6422, -0.1914,
 

Reduced Embedding for: 票价 
 tensor([[-0.2004,  0.1383, -0.2138,  0.1462, -0.3838,  0.0346,  0.2289, -0.1826,
          0.2696,  0.0392,  0.0187,  0.0811,  0.1836,  0.1957, -0.2809, -0.1913,
          0.0682, -0.2143, -0.1856,  0.1225, -0.2988,  0.3143, -0.0665, -0.0875,
          0.1556,  0.1959, -0.0919,  0.1398, -0.1349,  0.0135,  0.3115, -0.2536,
          0.0418,  0.0528,  0.2006, -0.0058, -0.0484,  0.4855,  0.3336,  0.1835,
          0.2837,  0.1416, -0.0803,  0.0767,  0.0779,  0.1575, -0.2149,  0.1178,
         -0.4113, -0.3034, -0.1510, -0.3750,  0.1543, -0.5408, -0.3763, -0.2244,
          0.2776, -0.0820,  0.1235, -0.1407, -0.1643, -0.3049,  0.0164,  0.1345,
          0.0680, -0.3875, -0.5988, -0.3731, -0.2582,  0.0856, -0.2404, -0.3668,
         -0.0955,  0.2279,  0.1131, -0.1788,  0.1872, -0.1489,  0.0386,  0.2437,
          0.2021, -0.3845, -0.2714,  0.1689,  0.1563,  0.4958, -0.0210,  0.5296,
         -0.2756, -0.1721, -0.2947,  0.1137, -0.1358, -0.2043,  0.6065, -0.2425,


KeyboardInterrupt: 

In [ ]:
import torch
import torch.nn as nn
from transformers import RobertaModel, RobertaTokenizer
import json
import numpy as np

class BiLSTM(nn.Module):
    def __init__(self, input_dim, hidden_dim, num_layers):
        super(BiLSTM, self).__init__()
        self.hidden_dim = hidden_dim
        self.num_layers = num_layers
        
        # 双向LSTM
        self.lstm = nn.LSTM(input_dim, hidden_dim, num_layers, batch_first=True, bidirectional=True)
        
        # 线性层，由于LSTM是双向的，因此最终的特征维度是hidden_dim的两倍
        #self.linear = nn.Linear(hidden_dim * 2, output_dim)

    def forward(self, x):
        # 初始化隐藏状态和细胞状态
        h0 = torch.zeros(self.num_layers * 2, x.size(0), self.hidden_dim).to(x.device)  # 2 for bidirection
        c0 = torch.zeros(self.num_layers * 2, x.size(0), self.hidden_dim).to(x.device)
        
        # 从LSTM获取所有隐藏状态
        out, (hn, cn) = self.lstm(x, (h0, c0))

        return out, hn, cn

model_bilstm = BiLSTM(input_dim=300, hidden_dim=300, num_layers=2)

# 定义一个线性层用于从768维降到300维
linear = torch.nn.Linear(768, 300)

# 加载 RoBERTa 模型和 tokenizer
tokenizer = RobertaTokenizer.from_pretrained('E:\\papercode\\model\\roberta-base', ignore_mismatched_sizes=True)
model = RobertaModel.from_pretrained('E:\\papercode\\model\\roberta-base')

# 读取.json数据集
with open('E:\\papercode\\Train\\train_data.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

keywords_to_hidden_states ={}

for item in data:
    keywords = item['keyword_result']
    embeddings = []  # 用于存储每个关键词处理后的向量
    
    for keyword in keywords:
        # 对每个词进行word embedding
        inputs = tokenizer(keyword, return_tensors='pt', padding='max_length', max_length=512, truncation=True)
        outputs = model(**inputs)

        # 取最后一层的隐藏状态的平均值获取词级的向量表示
        word_embedding_avg = outputs.last_hidden_state.mean(dim=1)

        # 使用线性层从768维降维到300维
        reduced_embedding = linear(word_embedding_avg)
        
        embeddings.append(reduced_embedding)
    
    # 将embeddings列表转换为Tensor，以便输入到双向LSTM网络
    embeddings_tensor = torch.stack(embeddings).squeeze(1)  # 假设每个关键词处理后是1x300维，我们需要去掉多余的维度
    
    # 输入到双向LSTM网络
    lstm_outputs, hidden_states, cell_states = model_bilstm(embeddings_tensor.unsqueeze(0))  # 增加一个批次维度
    
    lstm_output = lstm_outputs.squeeze(0)

#     print(lstm_outputs)
    
    for idx, keyword in enumerate(keywords):
        # 存储关键词和对应的隐藏层状态向量
        keywords_to_hidden_states[keyword] = lstm_output[idx]
        
        print(keywords_to_hidden_states)

# lstm_outputs

In [1]:
import json

with open('E:\\papercode\\Test\\test_data.json', 'r', encoding='utf-8') as f:
    data1 = json.load(f)

with open('E:\\papercode\\Test\\semantic_dependency_analysis_results_test.json', 'r', encoding='utf-8') as f:
    data2 = json.load(f)
    

# 假设data1和data2都是记录的列表，并且顺序匹配
for record1, record2 in zip(data1, data2):
    # 确定每条记录的'sentence'是否相匹配
    if record1['sentence'] == record2['sentence']:
        # 将'triples'添加进第一份文件的每条记录中
        record1['triples'] = record2['triples']
    else:
        # 如果某条记录不匹配，则输出错误信息
        print(f"Error: Sentences do not match: {record1['sentence']} != {record2['sentence']}")

# 保存更新后的内容回第一个文件，或者保存到一个新的文件
with open("test.json", 'w') as f:
    json.dump(data1, f, indent=4)

In [3]:
import json

with open('E:\\papercode\\Train\\train_data.json', 'r', encoding='utf-8') as f:
    data = json.load(f)
    
for item in data:
    keywords = item['keyword_result']  # 每条数据中的关键词列表
    triples = item['triples']  # 每条数据中的依存关系列表

    # 创建一个字典来存储每个关键词及其依存关系
    dependency_dict = {}

    for keyword in keywords:
        # 查找当前关键词的所有依存关系
        current_dependencies = [triple for triple in triples if triple[0] == keyword]
        
        if current_dependencies:
            # 如果当前关键词有依存关系，则存储相关信息
            dependency_dict[keyword] = current_dependencies
        else:
            # 如果没有依存关系就跳过
            continue
    for keyword, dependencies in dependency_dict.items():
        print(f"关键词：{keyword}, 依存关系：{dependencies}")


关键词：产量, 依存关系：[['产量', '及其', 'mRELA'], ['产量', '平均', 'FEAT'], ['产量', '每亩', 'SCO']]
关键词：作物, 依存关系：[['作物', '转基因', 'FEAT']]
关键词：农场, 依存关系：[['农场', '所有', 'SCO'], ['农场', '种植', 'rAGT'], ['农场', '产量', 'eCOO']]
关键词：种植, 依存关系：[['种植', '作物', 'CONT'], ['种植', '的', 'mDEPD']]
关键词：A, 依存关系：[['A', '以', 'mRELA']]
关键词：人员, 依存关系：[['人员', '结尾', 'rEXP'], ['人员', '活动', 'FEAT']]
关键词：姓名, 依存关系：[['姓名', '角色', 'eCOO']]
关键词：结尾, 依存关系：[['结尾', 'A', 'EXP'], ['结尾', '的', 'mDEPD']]
关键词：角色, 依存关系：[['角色', '人员', 'FEAT']]
关键词：低于, 依存关系：[['低于', '票价', 'EXP'], ['低于', '元', 'MEAS'], ['低于', '的', 'mDEPD']]
关键词：名称, 依存关系：[['名称', '低于', 'dFEAT'], ['名称', '电影', 'FEAT'], ['名称', '票价', 'eCOO']]
关键词：票价, 依存关系：[['票价', '所有', 'SCO'], ['票价', '电影', 'FEAT'], ['票价', '和', 'mRELA']]
关键词：员工, 依存关系：[['员工', '的', 'mDEPD']]
关键词：年龄, 依存关系：[['年龄', '员工', 'FEAT'], ['年龄', '平均', 'FEAT']]
关键词：表, 依存关系：[['表', '员工', 'FEAT'], ['表', '中', 'mDEPD']]
关键词：E4567, 依存关系：[['E4567', '或', 'mRELA'], ['E4567', 'employee_id ', 'FEAT'], ['E4567', '的', 'mDEPD']]
关键词：OU003, 依存关系：[['OU003', 'E4567', '

关键词：面积, 依存关系：[['面积', '及其', 'mRELA'], ['面积', '覆盖', 'rLOC']]
关键词：它们, 依存关系：[['它们', '的', 'mDEPD']]
关键词：导演, 依存关系：[['导演', '和', 'mRELA'], ['导演', '它们', 'FEAT']]
关键词：电影, 依存关系：[['电影', '评分', 'FEAT'], ['电影', '导演', 'eCOO']]
关键词：评分, 依存关系：[['评分', '最高', 'FEAT'], ['评分', '的', 'mDEPD']]
关键词：E9012, 依存关系：[['E9012', '或', 'mRELA'], ['E9012', 'employee_id ', 'FEAT'], ['E9012', '的', 'mDEPD']]
关键词：OU065, 依存关系：[['OU065', 'official_user_id ', 'FEAT'], ['OU065', 'E9012', 'eCOO']]
关键词：员工, 依存关系：[['员工', '所有', 'SCO'], ['员工', 'OU065', 'FEAT']]
关键词：创建, 依存关系：[['创建', '用户', 'AGT'], ['创建', '的', 'mDEPD']]
关键词：包含, 依存关系：[['包含', '描述', 'EXP'], ['包含', '词', 'LINK'], ['包含', '的', 'mDEPD']]
关键词：危险, 依存关系：[['危险', '创建', 'rCONT'], ['危险', '包含', 'dFEAT']]
关键词：用户, 依存关系：[['用户', '由', 'mRELA'], ['用户', '特定', 'FEAT']]
关键词：词, 依存关系：[['词', '化学品', 'FEAT'], ['词', '一', 'MEAS']]
关键词：名称, 依存关系：[['名称', '机构', 'FEAT'], ['名称', '领域', 'eCOO']]
关键词：机构, 依存关系：[['机构', '所有', 'SCO'], ['机构', '研究', 'FEAT'], ['机构', '的', 'mDEPD']]
关键词：领域, 依存关系：[['领域', '和', 'mRELA'], ['领

关键词：状态, 依存关系：[['状态', '活动', 'FEAT']]
关键词：资产, 依存关系：[['资产', '为', 'dFEAT']]
关键词：信息, 依存关系：[['信息', '超过', 'dFEAT'], ['信息', '阅览室', 'DATV']]
关键词：插座, 依存关系：[['插座', '所有', 'SCO']]
关键词：数量, 依存关系：[['数量', '插座', 'FEAT']]
关键词：超过, 依存关系：[['超过', '数量', 'EXP'], ['超过', '个', 'MEAS'], ['超过', '的', 'mDEPD']]
关键词：事件, 依存关系：[['事件', '大于', 'dFEAT']]
关键词：大于, 依存关系：[['大于', 'harmt', 'EXP'], ['大于', '100', 'STAT'], ['大于', '设置', 'eSUCC']]
关键词：设置, 依存关系：[['设置', '或', 'mRELA'], ['设置', 'is_open', 'EXP'], ['设置', '为', 'eSUCC'], ['设置', '的', 'mDEPD']]
关键词：10点, 依存关系：[['10点', '晚上', 'FEAT']]
关键词：名称, 依存关系：[['名称', '图书馆', 'FEAT'], ['名称', '地址', 'eCOO']]
关键词：图书馆, 依存关系：[['图书馆', '所有', 'SCO'], ['图书馆', '开放', 'rEXP']]
关键词：地址, 依存关系：[['地址', '和', 'mRELA']]
关键词：开放, 依存关系：[['开放', '直到', 'eSUCC'], ['开放', '10点', 'TIME'], ['开放', '的', 'mDEPD']]
关键词：AT174, 依存关系：[['AT174', 'asset_type_id ', 'FEAT']]
关键词：AT175, 依存关系：[['AT175', '或 ', 'mRELA'], ['AT175', 'asset_type_id ', 'FEAT'], ['AT175', '的', 'mDEPD']]
关键词：资产, 依存关系：[['资产', 'AT174', 'FEAT'], ['资产', 'AT175', 'FE

关键词：作物, 依存关系：[['作物', '及其', 'mRELA'], ['作物', '的', 'mDEPD']]
关键词：使用, 依存关系：[['使用', '助手', 'PAT'], ['使用', '进行', 'eSUCC'], ['使用', '的', 'mDEPD']]
关键词：农场, 依存关系：[['农场', '所有', 'SCO'], ['农场', '使用', 'rAGT']]
关键词：助手, 依存关系：[['助手', '机器人', 'FEAT']]
关键词：管理, 依存关系：[['管理', '农作物', 'PAT']]
关键词：进行, 依存关系：[['进行', '管理', 'CONT']]
关键词：加工厂, 依存关系：[['加工厂', '所有', 'SCO'], ['加工厂', '通过', 'rEXP'], ['加工厂', '农产品', 'FEAT'], ['加工厂', '加工量', 'eCOO']]
关键词：加工量, 依存关系：[['加工量', '及其', 'mRELA'], ['加工量', '年', 'MEAS']]
关键词：认证, 依存关系：[['认证', '有机', 'MANN']]
关键词：通过, 依存关系：[['通过', '认证', 'CONT'], ['通过', '的', 'mDEPD']]
关键词：书籍, 依存关系：[['书籍', '所有', 'SCO'], ['书籍', '低于', 'dFEAT']]
关键词：低于, 依存关系：[['低于', '价格', 'EXP'], ['低于', '50', 'MEAS'], ['低于', '的', 'mDEPD']]
关键词：标题, 依存关系：[['标题', '书籍', 'FEAT']]
关键词：名称, 依存关系：[['名称', '歌曲', 'FEAT'], ['名称', '歌手', 'eCOO']]
关键词：歌手, 依存关系：[['歌手', '和', 'mRELA']]
关键词：歌曲, 依存关系：[['歌曲', '所有', 'SCO'], ['歌曲', '的', 'mDEPD']]
关键词：员工, 依存关系：[['员工', '的', 'mDEPD']]
关键词：工资, 依存关系：[['工资', '员工', 'FEAT'], ['工资', '平均', 'FEAT']]
关键词：表, 依存关系：[[

In [2]:
import json

with open('E:\\papercode\\Train\\train_data.json', 'r', encoding='utf-8') as f:
    data = json.load(f)
    
data

[{'sentence': '查询所有种植转基因作物的农场及其平均每亩产量',
  'keyword_result': ['产量', '作物', '农场', '及其', '平均', '所有', '每亩', '种植', '转基因'],
  'triples': [['农场', '所有', 'SCO'],
   ['农场', '种植', 'rAGT'],
   ['作物', '转基因', 'FEAT'],
   ['种植', '作物', 'CONT'],
   ['种植', '的', 'mDEPD'],
   ['查询', '农场', 'CONT'],
   ['产量', '及其', 'mRELA'],
   ['产量', '平均', 'FEAT'],
   ['产量', '每亩', 'SCO'],
   ['农场', '产量', 'eCOO']]},
 {'sentence': '检索姓名以“A”结尾的活动人员角色',
  'keyword_result': ['A', '人员', '以', '姓名', '活动', '结尾', '角色'],
  'triples': [['检索', '姓名', 'CONT'],
   ['A', '以', 'mRELA'],
   ['结尾', 'A', 'EXP'],
   ['人员', '结尾', 'rEXP'],
   ['结尾', '的', 'mDEPD'],
   ['人员', '活动', 'FEAT'],
   ['角色', '人员', 'FEAT'],
   ['姓名', '角色', 'eCOO']]},
 {'sentence': '找出所有电影票价低于50元的电影名称和票价',
  'keyword_result': ['50', '低于', '出', '名称', '和', '所有', '电影', '票价'],
  'triples': [['找', '出', 'mDEPD'],
   ['票价', '所有', 'SCO'],
   ['票价', '电影', 'FEAT'],
   ['低于', '票价', 'EXP'],
   ['名称', '低于', 'dFEAT'],
   ['元', '50', 'MEAS'],
   ['低于', '元', 'MEAS'],
   ['低于', '的', 'mDEPD'],

In [3]:
import pandas as pd

data = pd.read_csv('IMDB Dataset.csv')

data['review'].head()

UnicodeDecodeError: 'utf-8' codec can't decode bytes in position 200844-200845: invalid continuation byte